# Support Vector Machine (SMV), Cesar Avellaneda, 2202214746

Esto corresponde al noteBook del algoritmo SMV, a cargo de Cesar Avellaneda:

Y contiene los siguientes elementos:
1. Cargue de los datos.

2. Entendimiento de los datos: Describir las características más relevantes de los datos y todo el perfilamiento de datos, incluir el análisis de calidad de datos y hacer una preselección de las variables más importantes para la etapa de modelado.

3. Preparación de datos: Solucionar los problemas de calidad de datos previamente identificados que afecten el modelo a construir. Además, debe aplicar todos los proceso de preprocesamiento de datos necesarios para la construcción del modelo de regresión.

4. Modelado: Utilizando las variables previamente seleccionadas, construir un modelo de regresión que estime la variable objetivo con el menor error posible.


# Entendimiento del Problema:

El problema principal radica en la necesidad de analizar de forma eficiente y automática grandes volúmenes de opiniones en lenguaje natural para relacionarlas con los ODS 3 (Salud y Bienestar), 4 (Educación de Calidad) y 5 (Igualdad de Género). Actualmente, este proceso es manual y requiere la intervención de expertos, lo que lo hace costoso y lento. La oportunidad consiste en desarrollar un modelo analítico automatizado que reduzca el tiempo y los recursos necesarios para este análisis, permitiendo una respuesta más rápida y efectiva a las necesidades de los ciudadanos.

# Enfoque Analitico:

Categoría de Análisis:
El análisis será predictivo y descriptivo. Descriptivo en el sentido de identificar y categorizar opiniones actuales, y predictivo al inferir tendencias y futuras necesidades o áreas de intervención.

Tipo y Tarea de Aprendizaje:
Aprendizaje Supervisado: Para clasificar las opiniones y relacionarlas con los ODS.

Técnicas y Algoritmos:
Modelos de Clasificación: SVM (Support Vector Machines).

# 1. Carga de los Datos:

In [53]:
import inflect
import nltk
nltk.download('punkt')
nltk.download('punkt_tab')
nltk.download('stopwords')
nltk.download('wordnet')
import pandas as pd
import numpy as np
import sys
import re, string, unicodedata
from nltk import word_tokenize, sent_tokenize
from nltk.corpus import stopwords
from nltk.stem import LancasterStemmer, WordNetLemmatizer
from sklearn.model_selection import train_test_split,GridSearchCV
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer, HashingVectorizer
from sklearn.pipeline import Pipeline, FeatureUnion
from sklearn.svm import SVC
from sklearn.ensemble import BaggingClassifier, RandomForestClassifier, AdaBoostClassifier
from sklearn.naive_bayes import BernoulliNB
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.base import BaseEstimator, ClassifierMixin
import matplotlib.pyplot as plt

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\cesar\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package punkt_tab to
[nltk_data]     C:\Users\cesar\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\cesar\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\cesar\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [54]:
entrevistasODS = pd.read_excel('./data/ODScat_345.xlsx')

# 2. Perfilamiento y entendimiento de datos:

In [55]:
print(entrevistasODS.head())

                                      Textos_espanol  sdg
0  Por ejemplo, el nÃºmero de consultas externas ...    3
1  En 2007, el gobierno central financió directam...    3
2  Claramente, hay muchos otros factores en juego...    3
3  Por ejemplo, el estado australiano de Victoria...    3
4  El consumo anual de alcohol se estima en 15,7 ...    3


In [56]:
entrevistasODS.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4049 entries, 0 to 4048
Data columns (total 2 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   Textos_espanol  4049 non-null   object
 1   sdg             4049 non-null   int64 
dtypes: int64(1), object(1)
memory usage: 63.4+ KB


In [57]:
entrevistadosCopy = entrevistasODS.copy()
entrevistadosCopy['Conteo'] = [len(x) for x in entrevistadosCopy['Textos_espanol']]
#entrevistadosCopy['Moda'] =
entrevistadosCopy['Max'] = [[max([len(x) for x in i.split(' ')])][0] for i in entrevistadosCopy['Textos_espanol']]
entrevistadosCopy['Min'] = [[min([len(x) for x in i.split(' ')])][0] for i in entrevistadosCopy['Textos_espanol']]


In [58]:
entrevistadosCopy

Textos_espanol  sdg  Conteo  Max  Min
0     Por ejemplo, el nÃºmero de consultas externas ...    3     944   18    1
1     En 2007, el gobierno central financió directam...    3     476   14    1
2     Claramente, hay muchos otros factores en juego...    3    1207   15    1
3     Por ejemplo, el estado australiano de Victoria...    3    1090   17    1
4     El consumo anual de alcohol se estima en 15,7 ...    3     895   13    1
...                                                 ...  ...     ...  ...  ...
4044  Para ello, identificará las cuestiones de géne...    5     822   16    1
4045  La participación de las mujeres en roles de li...    5     514   16    1
4046  Según el WEF, según las tendencias de 2016, po...    5     445   17    1
4047  Sirve como recurso y foro para las agencias, c...    5    1017   15    1
4048  Las áreas útiles para un mayor estudio y acció...    5     728   15    1

[4049 rows x 5 columns]

# 3. Limpieza de Datos:

In [59]:
def remove_non_ascii(words):
    """Remove non-ASCII characters from list of tokenized words"""
    new_words = []
    for word in words:
        if word is not None:
          new_word = unicodedata.normalize('NFKD', word).encode('ascii', 'ignore').decode('utf-8', 'ignore')
          new_words.append(new_word)
    return new_words

def to_lowercase(words):
    new_words=[]
    for word in words:
        w= word.lower()
        new_words.append(w)
    return new_words

def remove_punctuation(words):
    """Remove punctuation from list of tokenized words"""
    new_words = []
    for word in words:
        if word is not None:
            new_word = re.sub(r'[^\w\s]', '', word)
            if new_word != '':
                new_words.append(new_word)
    return new_words

def replace_numbers(words):
    """Replace all interger occurrences in list of tokenized words with textual representation"""
    p = inflect.engine()    
    print(words)
    new_words = []
    for word in words:
        if word.isdigit():
            new_word = p.number_to_words(word)
            new_words.append(new_word)
            print("if " + new_word)
        else:
            new_words.append(word)
    return new_words

def remove_stopwords(words):
    spanish_sw = set(stopwords.words('spanish'))
    new_words = []
    for word in words:
        if word not in spanish_sw:
            new_words.append(word)
    return new_words


def preprocessing(words):
    words = to_lowercase(words)
    words = replace_numbers(words)
    words = remove_punctuation(words)
    words = remove_non_ascii(words)
    words = remove_stopwords(words)
    return words

In [60]:
entrevistasODS['palabras'] = entrevistasODS['Textos_espanol'].apply(word_tokenize)
entrevistasODS.head()

Textos_espanol  sdg  \
0  Por ejemplo, el nÃºmero de consultas externas ...    3   
1  En 2007, el gobierno central financió directam...    3   
2  Claramente, hay muchos otros factores en juego...    3   
3  Por ejemplo, el estado australiano de Victoria...    3   
4  El consumo anual de alcohol se estima en 15,7 ...    3   

                                            palabras  
0  [Por, ejemplo, ,, el, nÃºmero, de, consultas, ...  
1  [En, 2007, ,, el, gobierno, central, financió,...  
2  [Claramente, ,, hay, muchos, otros, factores, ...  
3  [Por, ejemplo, ,, el, estado, australiano, de,...  
4  [El, consumo, anual, de, alcohol, se, estima, ...

In [61]:
entrevistasODS['palabras'].dropna()

0       [Por, ejemplo, ,, el, nÃºmero, de, consultas, ...
1       [En, 2007, ,, el, gobierno, central, financió,...
2       [Claramente, ,, hay, muchos, otros, factores, ...
3       [Por, ejemplo, ,, el, estado, australiano, de,...
4       [El, consumo, anual, de, alcohol, se, estima, ...
                              ...                        
4044    [Para, ello, ,, identificará, las, cuestiones,...
4045    [La, participación, de, las, mujeres, en, role...
4046    [Según, el, WEF, ,, según, las, tendencias, de...
4047    [Sirve, como, recurso, y, foro, para, las, age...
4048    [Las, áreas, útiles, para, un, mayor, estudio,...
Name: palabras, Length: 4049, dtype: object

In [62]:
entrevistasODS['palabras'].info()

<class 'pandas.core.series.Series'>
RangeIndex: 4049 entries, 0 to 4048
Series name: palabras
Non-Null Count  Dtype 
--------------  ----- 
4049 non-null   object
dtypes: object(1)
memory usage: 31.8+ KB


In [63]:
entrevistasODS['palabras1']=entrevistasODS['palabras'].apply(preprocessing)
entrevistasODS.head()

['por', 'ejemplo', ',', 'el', 'nãºmero', 'de', 'consultas', 'externas', 'de', 'especialistas', 'es', 'de', '319', 'por', 'cada', 'mil', 'derechohabientes', 'en', 'el', 'sp', ',', 'en', 'comparaciã³n', 'con', '338', 'y', '620', 'por', 'cada', 'mil', 'derechohabientes', 'en', 'el', 'imss', 'y', 'el', 'issste', ',', 'respectivamente', '.', 'si', 'bien', 'algunas', 'de', 'estas', 'diferencias', 'pueden', 'reflejar', 'una', 'necesidad', 'desigual', '(', 'como', 'la', 'poblaciã³n', 'ligeramente', 'mayor', 'del', 'issste', ')', ',', 'otras', 'no', 'pueden', 'justificarse', 'de', 'esta', 'manera', '.', 'el', 'nãºmero', 'de', 'recetas', 'que', 'no', 'pudieron', 'ser', 'surtidas', 'en', 'su', 'totalidad', 'por', 'un', 'farmacã©utico', 'debido', 'a', 'la', 'falta', 'de', 'existencias', 'es', 'de', '33', '%', 'dentro', 'del', 'sp', 'en', 'comparaciã³n', 'con', '14', '%', 'dentro', 'del', 'imss', 'segãºn', 'los', 'datos', 'de', 'la', 'encuesta', '(', 'aunque', 'las', 'propias', 'cifras', 'de', 'los

Textos_espanol  sdg  \
0  Por ejemplo, el nÃºmero de consultas externas ...    3   
1  En 2007, el gobierno central financió directam...    3   
2  Claramente, hay muchos otros factores en juego...    3   
3  Por ejemplo, el estado australiano de Victoria...    3   
4  El consumo anual de alcohol se estima en 15,7 ...    3   

                                            palabras  \
0  [Por, ejemplo, ,, el, nÃºmero, de, consultas, ...   
1  [En, 2007, ,, el, gobierno, central, financió,...   
2  [Claramente, ,, hay, muchos, otros, factores, ...   
3  [Por, ejemplo, ,, el, estado, australiano, de,...   
4  [El, consumo, anual, de, alcohol, se, estima, ...   

                                           palabras1  
0  [ejemplo, naomero, consultas, externas, especi...  
1  [two thousand and seven, gobierno, central, fi...  
2  [claramente, factores, juego, particular, vari...  
3  [ejemplo, australiano, victoria, creo, agencia...  
4  [consumo, anual, alcohol, estima, 157, litros,...

In [64]:
entrevistasODS['palabras'] = entrevistasODS['palabras'].apply(lambda x: ' '.join(map(str, x)))
entrevistasODS

Textos_espanol  sdg  \
0     Por ejemplo, el nÃºmero de consultas externas ...    3   
1     En 2007, el gobierno central financió directam...    3   
2     Claramente, hay muchos otros factores en juego...    3   
3     Por ejemplo, el estado australiano de Victoria...    3   
4     El consumo anual de alcohol se estima en 15,7 ...    3   
...                                                 ...  ...   
4044  Para ello, identificará las cuestiones de géne...    5   
4045  La participación de las mujeres en roles de li...    5   
4046  Según el WEF, según las tendencias de 2016, po...    5   
4047  Sirve como recurso y foro para las agencias, c...    5   
4048  Las áreas útiles para un mayor estudio y acció...    5   

                                               palabras  \
0     Por ejemplo , el nÃºmero de consultas externas...   
1     En 2007 , el gobierno central financió directa...   
2     Claramente , hay muchos otros factores en jueg...   
3     Por ejemplo , el estado australiano de Victori...   
4     El consumo anual de alcohol se estima en 15,7 ...   
...                                                 ...   
4044  Para ello , identificará las cuestiones de gén...   
4045  La participación de las mujeres en roles de li...   
4046  Según el WEF , según las tendencias de 2016 , ...   
4047  Sirve como recurso y foro para las agencias , ...   
4048  Las áreas útiles para un mayor estudio y acció...   

                                              palabras1  
0     [ejemplo, naomero, consultas, externas, especi...  
1     [two thousand and seven, gobierno, central, fi...  
2     [claramente, factores, juego, particular, vari...  
3     [ejemplo, australiano, victoria, creo, agencia...  
4     [consumo, anual, alcohol, estima, 157, litros,...  
...                                                 ...  
4044  [ello, identificara, cuestiones, genero, mas, ...  
4045  [participacion, mujeres, roles, liderazgo, den...  
4046  [segun, wef, segun, tendencias, two thousand a...  
4047  [sirve, recurso, foro, agencias, objetivo, log...  
4048  [areas, utiles, mayor, estudio, accion, politi...  

[4049 rows x 4 columns]

In [65]:
X_data, y_data = entrevistasODS['palabras'],entrevistasODS['sdg']
y_data

0       3
1       3
2       3
3       3
4       3
       ..
4044    5
4045    5
4046    5
4047    5
4048    5
Name: sdg, Length: 4049, dtype: int64

In [66]:
dummy = CountVectorizer(binary=True)
X_dummy = dummy.fit_transform(X_data)
print(X_dummy.shape)
X_dummy.toarray()[0]

(4049, 20558)


array([0, 0, 0, ..., 0, 0, 0])

In [67]:
count = CountVectorizer()
X_count = count.fit_transform(X_data)
print(X_count.shape)
X_count.toarray()[0]

(4049, 20558)


array([0, 0, 0, ..., 0, 0, 0])

# SMV

In [68]:
X_train, X_test, y_train, y_test = train_test_split(X_count, y_data, test_size=0.2, random_state=42)
svm_model = SVC(kernel='linear')
svm_model.fit(X_train, y_train)
y_pred = svm_model.predict(X_test)
print(classification_report(y_test, y_pred))
print(confusion_matrix(y_test, y_pred))


              precision    recall  f1-score   support

           3       0.97      0.98      0.98       250
           4       0.99      0.97      0.98       268
           5       0.98      0.98      0.98       292

    accuracy                           0.98       810
   macro avg       0.98      0.98      0.98       810
weighted avg       0.98      0.98      0.98       810

[[246   1   3]
 [  4 260   4]
 [  4   2 286]]


# Bolsa de Palabras

In [69]:
X_count = count.fit_transform(X_data)
y_pred = svm_model.predict(X_test)
print(classification_report(y_test, y_pred))
print(confusion_matrix(y_test, y_pred))

param_grid = {'C': [0.1, 1, 10], 'kernel': ['linear', 'rbf', 'poly'], 'gamma': ['scale', 'auto']}
grid = GridSearchCV(SVC(), param_grid, refit=True, verbose=2)
grid.fit(X_train, y_train)
print("Mejores parámetros:", grid.best_params_)
y_pred = grid.predict(X_test)
print(classification_report(y_test, y_pred))
print(confusion_matrix(y_test, y_pred))


              precision    recall  f1-score   support

           3       0.97      0.98      0.98       250
           4       0.99      0.97      0.98       268
           5       0.98      0.98      0.98       292

    accuracy                           0.98       810
   macro avg       0.98      0.98      0.98       810
weighted avg       0.98      0.98      0.98       810

[[246   1   3]
 [  4 260   4]
 [  4   2 286]]
Fitting 5 folds for each of 18 candidates, totalling 90 fits
[CV] END ..................C=0.1, gamma=scale, kernel=linear; total time=   1.9s
[CV] END ..................C=0.1, gamma=scale, kernel=linear; total time=   1.8s
[CV] END ..................C=0.1, gamma=scale, kernel=linear; total time=   1.8s
[CV] END ..................C=0.1, gamma=scale, kernel=linear; total time=   1.8s
[CV] END ..................C=0.1, gamma=scale, kernel=linear; total time=   1.8s
[CV] END .....................C=0.1, gamma=scale, kernel=rbf; total time=   5.5s
[CV] END .................

KeyboardInterrupt: 